# Create AMITT website sql

Creates the sqlite file used as a datasource in the AMITT website tests. 

In [1]:
# Get AMITT variables

import pandas as pd
import sqlite3 as sql
from generate_amitt_ttps import Amitt
pd.set_option('display.max_rows', 1000)


# Generate AMITT datasets
amitt = Amitt()

# Check which amitt variables we can see from here
print('{}'.format(vars(amitt).keys()))
vars(amitt)['cross_counterid_techniqueid']

dict_keys(['df_phases', 'df_frameworks', 'df_techniques', 'df_tasks', 'df_incidents', 'df_counters', 'df_detections', 'df_actortypes', 'df_resources', 'df_responsetypes', 'df_metatechniques', 'it', 'df_tactics', 'df_techniques_per_tactic', 'df_counters_per_tactic', 'phases', 'tactics', 'techniques', 'counters', 'metatechniques', 'actortypes', 'resources', 'num_tactics', 'cross_counterid_techniqueid', 'cross_counterid_resourceid', 'cross_counterid_actortypeid'])


amitt_id technique_id
0     C00006        T0007
0     C00006        T0015
0     C00006        T0018
0     C00006        T0043
0     C00006        T0053
0     C00006        T0054
0     C00006             
1     C00008        T0001
1     C00008        T0002
1     C00008        T0003
1     C00008        T0027
1     C00008        T0028
1     C00008        T0006
1     C00008        T0009
1     C00008        T0008
1     C00008        T0013
1     C00008        T0014
1     C00008        T0021
1     C00008        T0025
1     C00008        T0024
1     C00008        T0026
1     C00008        T0056
1     C00008        T0051
1     C00008        T0044
1     C00008        T0045
2     C00009        T0010
2     C00009        T0039
2     C00009        T0044
2     C00009        T0042
2     C00009        T0048
2     C00009        T0052
2     C00009        T0053
2     C00009        T0055
2     C00009        T0056
3     C00010        T0005
3     C00010        T0018
4     C00011        T0001
4     C00011        T0002
4     C00011        T0003
4     C00011        T0027
4     C00011        T0028
4     C00011        T0006
4     C00011        T0009
4     C00011        T0008
4     C00011        T0013
4     C00011        T0021
4     C00011        T0025
4     C00011        T0024
4     C00011        T0026
4     C00011        T0056
4     C00011        T0051
4     C00011        T0044
4     C00011        T0045
5     C00012        T0001
5     C00012        T0002
5     C00012        T0003
5     C00012        T0007
5     C00012        T0008
5     C00012        T0009
5     C00012        T0013
5     C00012        T0014
5     C00012        T0015
5     C00012        T0016
5     C00012        T0017
5     C00012        T0018
5     C00012        T0021
5     C00012        T0022
5     C00012        T0024
5     C00012        T0025
5     C00012        T0026
5     C00012        T0043
5     C00012        T0045
5     C00012        T0046
5     C00012        T0047
5     C00012        T0048
5     C00012        T0049
5     C00012        T0050
5     C00012        T0051
5     C00012        T0052
5     C00012        T0053
5     C00012        T0054
5     C00012        T0055
5     C00012        T0056
5     C00012        T0057
5     C00012        T0061
6     C00013        T0001
6     C00013        T0002
6     C00013        T0003
6     C00013        T0027
6     C00013        T0028
6     C00013        T0056
6     C00013        T0052
7     C00014        T0001
7     C00014        T0002
7     C00014        T0003
7     C00014        T0027
7     C00014        T0028
7     C00014        T0006
7     C00014        T0009
7     C00014        T0008
7     C00014        T0013
7     C00014        T0014
7     C00014        T0021
7     C00014        T0025
7     C00014        T0024
7     C00014        T0026
7     C00014        T0056
7     C00014        T0051
7     C00014        T0044
7     C00014        T0045
8     C00016        T0001
8     C00016        T0002
8     C00016        T0003
8     C00016        T0027
8     C00016        T0028
8     C00016        T0009
8     C00016        T0008
8     C00016        T0007
8     C00016        T0013
8     C00016        T0014
8     C00016        T0015
8     C00016        T0016
8     C00016        T0017
8     C00016        T0018
8     C00016        T0022
8     C00016        T0021
8     C00016        T0025
8     C00016        T0024
8     C00016        T0026
8     C00016        T0044
8     C00016        T0045
8     C00016        T0043
8     C00016        T0056
8     C00016        T0051
8     C00016        T0049
8     C00016        T0052
8     C00016        T0054
8     C00016        T0053
8     C00016        T0055
8     C00016        T0058
8     C00016        T0057
8     C00016             
9     C00017        T0001
9     C00017        T0002
9     C00017        T0003
9     C00017        T0027
9     C00017        T0028
9     C00017        T0022
9     C00017        T0023
10    C00019        T0001
10    C00019        T0002
10    C00019        T0003
10    C00019        T0027


In [2]:
# Generate minimal sqlite database from the Amitt variables
conn = sql.connect('amittsite.sqlite')

def add_table(dataframe, tablename, columns):    
    # Create sql table
    colnames = ', '.join(['{} TEXT NOT NULL'.format(col) for col in columns])
    conn.execute("DROP TABLE IF EXISTS {}".format(tablename))
    conn.execute('''CREATE TABLE {} (id INTEGER PRIMARY KEY AUTOINCREMENT, {});'''.format(tablename, colnames))
    #populate table from dataframe
    newtable = dataframe[columns].copy().applymap(str)
    newtable['id'] = range(1,len(newtable)+1)
    newtable.to_sql(tablename, conn, index=False, if_exists='append')
    conn.commit()
    return newtable

def counter_tactics_techniques():
    # techniques - counters
    ctech = amitt.cross_counterid_techniqueid[(amitt.cross_counterid_techniqueid['technique_id'] != '') & 
                                          (~amitt.cross_counterid_techniqueid['technique_id'].str.startswith('TA'))]
    ctech['summary'] = ''

    # tactics - counters
    ctact = amitt.cross_counterid_techniqueid[amitt.cross_counterid_techniqueid['technique_id'].str.startswith('TA')].copy()
    ctact.rename(columns={'amitt_id':'counter_id', 'technique_id': 'tactic_id'}, inplace=True)
    ctact['primary'] = 'N'
    ctactprimary = amitt.df_counters[['amitt_id', 'tactic_id']].copy()
    ctactprimary.rename(columns={'amitt_id':'counter_id'}, inplace=True)
    ctactprimary['primary'] = 'Y'
    ctact = pd.concat([ctact, ctactprimary], ignore_index=True, sort=False)
    ctact['summary'] = ''
    return(ctech, ctact)

#newtable = add_table(amitt.df_actortypes, 'actor_type', ['amitt_id', 'sector_id', 'framework_id', 'name', 'summary'])
# counter
newtable = add_table(amitt.df_counters, 'counter', ['amitt_id', 'tactic_id', 'metatechnique_id', 'name', 'summary'])
# dataset
newtable = add_table(amitt.df_frameworks, 'framework', ['amitt_id', 'name', 'summary'])
# incident
# metatechnique
newtable = add_table(amitt.df_metatechniques, 'metatechnique', ['amitt_id', 'name', 'summary'])
newtable = add_table(amitt.df_phases, 'phase', ['amitt_id', 'name', 'rank', 'summary'])
# playbook
# reference
# response_type
# sector
newtable = add_table(amitt.df_tactics, 'tactic', ['amitt_id', 'phase_id', 'name', 'rank', 'summary'])
newtable = add_table(amitt.df_tasks, 'task', ['amitt_id', 'tactic_id', 'framework_id', 'name', 'summary'])
newtable = add_table(amitt.df_techniques, 'technique', ['amitt_id', 'tactic_id', 'name', 'summary'])
# technique_counter
(ctech, ctact) = counter_tactics_techniques()
newtable = add_table(ctech, 'technique_counter', ['counter_id', 'technique_id', 'summary'])
newtable = add_table(ctact, 'tactic_counter', ['counter_id', 'tactic_id', 'primary', 'summary'])

conn.execute("DROP TABLE IF EXISTS {}".format('user'))
conn.execute('''CREATE TABLE user (id INTEGER PRIMARY KEY AUTOINCREMENT, username TEXT NOT NULL UNIQUE, password TEXT NOT NULL);''')

conn.close()
newtable

KeyError: "['name', 'counter_id', 'summary'] not in index"

In [3]:
ctech

amitt_id technique_id
0     C00006        T0007
0     C00006        T0015
0     C00006        T0018
0     C00006        T0043
0     C00006        T0053
0     C00006        T0054
1     C00008        T0001
1     C00008        T0002
1     C00008        T0003
1     C00008        T0027
1     C00008        T0028
1     C00008        T0006
1     C00008        T0009
1     C00008        T0008
1     C00008        T0013
1     C00008        T0014
1     C00008        T0021
1     C00008        T0025
1     C00008        T0024
1     C00008        T0026
1     C00008        T0056
1     C00008        T0051
1     C00008        T0044
1     C00008        T0045
2     C00009        T0010
2     C00009        T0039
2     C00009        T0044
2     C00009        T0042
2     C00009        T0048
2     C00009        T0052
2     C00009        T0053
2     C00009        T0055
2     C00009        T0056
3     C00010        T0005
3     C00010        T0018
4     C00011        T0001
4     C00011        T0002
4     C00011        T0003
4     C00011        T0027
4     C00011        T0028
4     C00011        T0006
4     C00011        T0009
4     C00011        T0008
4     C00011        T0013
4     C00011        T0021
4     C00011        T0025
4     C00011        T0024
4     C00011        T0026
4     C00011        T0056
4     C00011        T0051
4     C00011        T0044
4     C00011        T0045
5     C00012        T0001
5     C00012        T0002
5     C00012        T0003
5     C00012        T0007
5     C00012        T0008
5     C00012        T0009
5     C00012        T0013
5     C00012        T0014
5     C00012        T0015
5     C00012        T0016
5     C00012        T0017
5     C00012        T0018
5     C00012        T0021
5     C00012        T0022
5     C00012        T0024
5     C00012        T0025
5     C00012        T0026
5     C00012        T0043
5     C00012        T0045
5     C00012        T0046
5     C00012        T0047
5     C00012        T0048
5     C00012        T0049
5     C00012        T0050
5     C00012        T0051
5     C00012        T0052
5     C00012        T0053
5     C00012        T0054
5     C00012        T0055
5     C00012        T0056
5     C00012        T0057
5     C00012        T0061
6     C00013        T0001
6     C00013        T0002
6     C00013        T0003
6     C00013        T0027
6     C00013        T0028
6     C00013        T0056
6     C00013        T0052
7     C00014        T0001
7     C00014        T0002
7     C00014        T0003
7     C00014        T0027
7     C00014        T0028
7     C00014        T0006
7     C00014        T0009
7     C00014        T0008
7     C00014        T0013
7     C00014        T0014
7     C00014        T0021
7     C00014        T0025
7     C00014        T0024
7     C00014        T0026
7     C00014        T0056
7     C00014        T0051
7     C00014        T0044
7     C00014        T0045
8     C00016        T0001
8     C00016        T0002
8     C00016        T0003
8     C00016        T0027
8     C00016        T0028
8     C00016        T0009
8     C00016        T0008
8     C00016        T0007
8     C00016        T0013
8     C00016        T0014
8     C00016        T0015
8     C00016        T0016
8     C00016        T0017
8     C00016        T0018
8     C00016        T0022
8     C00016        T0021
8     C00016        T0025
8     C00016        T0024
8     C00016        T0026
8     C00016        T0044
8     C00016        T0045
8     C00016        T0043
8     C00016        T0056
8     C00016        T0051
8     C00016        T0049
8     C00016        T0052
8     C00016        T0054
8     C00016        T0053
8     C00016        T0055
8     C00016        T0058
8     C00016        T0057
9     C00017        T0001
9     C00017        T0002
9     C00017        T0003
9     C00017        T0027
9     C00017        T0028
9     C00017        T0022
9     C00017        T0023
10    C00019        T0001
10    C00019        T0002
10    C00019        T0003
10    C00019        T0027
10    C00019        T0028
10    C00019        T0022


In [4]:
ctact

counter_id tactic_id primary
0       C00028      TA07       N
1       C00028      TA08       N
2       C00028      TA09       N
3       C00028      TA10       N
4       C00060      TA07       N
5       C00062      TA01       N
6       C00062      TA02       N
7       C00062      TA03       N
8       C00062      TA04       N
9       C00062      TA05       N
10      C00062      TA06       N
11      C00062      TA07       N
12      C00062      TA08       N
13      C00062      TA09       N
14      C00062      TA10       N
15      C00062      TA11       N
16      C00062      TA12       N
17      C00078      TA07       N
18      C00092      TA07       N
19      C00092      TA08       N
20      C00093      TA07       N
21      C00124      TA08       N
22      C00124      TA09       N
23      C00133      TA07       N
24      C00133      TA09       N
25      C00133      TA10       N
26      C00135      TA07       N
27      C00135      TA09       N
28      C00135      TA10       N
29      C00136      TA08       N
30      C00136      TA09       N
31      C00136      TA10       N
32      C00140      TA05       N
33      C00140      TA09       N
34      C00140      TA10       N
35      C00142      TA05       N
36      C00142      TA09       N
37      C00142      TA10       N
38      C00142      TA11       N
39      C00149      TA12       N
40      C00006      TA01       Y
41      C00008      TA01       Y
42      C00009      TA02       Y
43      C00010      TA01       Y
44      C00011      TA02       Y
45      C00012      TA01       Y
46      C00013      TA01       Y
47      C00014      TA06       Y
48      C00016      TA01       Y
49      C00017      TA01       Y
50      C00019      TA01       Y
51      C00021      TA01       Y
52      C00022      TA01       Y
53      C00024      TA01       Y
54      C00026      TA01       Y
55      C00027      TA01       Y
56      C00028      TA02       Y
57      C00029      TA02       Y
58      C00030      TA02       Y
59      C00031      TA02       Y
60      C00032      TA06       Y
61      C00034      TA03       Y
62      C00036      TA03       Y
63      C00040      TA03       Y
64      C00042      TA03       Y
65      C00044      TA03       Y
66      C00046      TA03       Y
67      C00047      TA04       Y
68      C00048      TA03       Y
69      C00051      TA03       Y
70      C00052      TA04       Y
71      C00053      TA04       Y
72      C00056      TA04       Y
73      C00058      TA03       Y
74      C00059      TA04       Y
75      C00060      TA02       Y
76      C00062      TA04       Y
77      C00065      TA05       Y
78      C00066      TA05       Y
79      C00067      TA03       Y
80      C00070      TA02       Y
81      C00071      TA06       Y
82      C00072      TA06       Y
83      C00073      TA01       Y
84      C00074      TA06       Y
85      C00075      TA06       Y
86      C00076      TA06       Y
87      C00077      TA03       Y
88      C00078      TA06       Y
89      C00080      TA06       Y
90      C00081      TA06       Y
91      C00082      TA06       Y
92      C00084      TA06       Y
93      C00085      TA06       Y
94      C00086      TA06       Y
95      C00087      TA06       Y
96      C00090      TA07       Y
97      C00091      TA06       Y
98      C00092      TA02       Y
99      C00093      TA03       Y
100     C00094      TA06       Y
101     C00096      TA01       Y
102     C00097      TA07       Y
103     C00098      TA07       Y
104     C00099      TA07       Y
105     C00100      TA08       Y
106     C00101      TA07       Y
107     C00103      TA07       Y
108     C00105      TA07       Y
109     C00106      TA06       Y
110     C00107      TA06       Y
111     C00109      TA09       Y
112     C00111      TA01       Y
113     C00112      TA08       Y
114     C00113      TA08       Y
115     C00114      TA08       Y
116     C00115      TA08       Y
117     C00116      TA08       Y
118     C00117      TA08       Y
119     C00118      TA08       Y
120     C00

In [37]:
ctact['counter_id'].value_counts().sort_index()

C00006     1
C00008     1
C00009     1
C00010     1
C00011     1
C00012     1
C00013     1
C00014     1
C00016     1
C00017     1
C00019     1
C00021     1
C00022     1
C00024     1
C00026     1
C00027     1
C00028     5
C00029     1
C00030     1
C00031     1
C00032     1
C00034     1
C00036     1
C00040     1
C00042     1
C00044     1
C00046     1
C00047     1
C00048     1
C00051     1
C00052     1
C00053     1
C00056     1
C00058     1
C00059     1
C00060     2
C00062    13
C00065     1
C00066     1
C00067     1
C00070     1
C00071     1
C00072     1
C00073     1
C00074     1
C00075     1
C00076     1
C00077     1
C00078     2
C00080     1
C00081     1
C00082     1
C00084     1
C00085     1
C00086     1
C00087     1
C00090     1
C00091     1
C00092     3
C00093     2
C00094     1
C00096     1
C00097     1
C00098     1
C00099     1
C00100     1
C00101     1
C00103     1
C00105     1
C00106     1
C00107     1
C00109     1
C00111     1
C00112     1
C00113     1
C00114     1
C00115     1

counter_id tactic_id primary
0       C00028      TA07       N
1       C00028      TA08       N
2       C00028      TA09       N
3       C00028      TA10       N
4       C00060      TA07       N
5       C00062      TA01       N
6       C00062      TA02       N
7       C00062      TA03       N
8       C00062      TA04       N
9       C00062      TA05       N
10      C00062      TA06       N
11      C00062      TA07       N
12      C00062      TA08       N
13      C00062      TA09       N
14      C00062      TA10       N
15      C00062      TA11       N
16      C00062      TA12       N
17      C00078      TA07       N
18      C00092      TA07       N
19      C00092      TA08       N
20      C00093      TA07       N
21      C00124      TA08       N
22      C00124      TA09       N
23      C00133      TA07       N
24      C00133      TA09       N
25      C00133      TA10       N
26      C00135      TA07       N
27      C00135      TA09       N
28      C00135      TA10       N
29      C00136      TA08       N
30      C00136      TA09       N
31      C00136      TA10       N
32      C00140      TA05       N
33      C00140      TA09       N
34      C00140      TA10       N
35      C00142      TA05       N
36      C00142      TA09       N
37      C00142      TA10       N
38      C00142      TA11       N
39      C00149      TA12       N
40      C00006      TA01       Y
41      C00008      TA01       Y
42      C00009      TA02       Y
43      C00010      TA01       Y
44      C00011      TA02       Y
45      C00012      TA01       Y
46      C00013      TA01       Y
47      C00014      TA06       Y
48      C00016      TA01       Y
49      C00017      TA01       Y
50      C00019      TA01       Y
51      C00021      TA01       Y
52      C00022      TA01       Y
53      C00024      TA01       Y
54      C00026      TA01       Y
55      C00027      TA01       Y
56      C00028      TA02       Y
57      C00029      TA02       Y
58      C00030      TA02       Y
59      C00031      TA02       Y
60      C00032      TA06       Y
61      C00034      TA03       Y
62      C00036      TA03       Y
63      C00040      TA03       Y
64      C00042      TA03       Y
65      C00044      TA03       Y
66      C00046      TA03       Y
67      C00047      TA04       Y
68      C00048      TA03       Y
69      C00051      TA03       Y
70      C00052      TA04       Y
71      C00053      TA04       Y
72      C00056      TA04       Y
73      C00058      TA03       Y
74      C00059      TA04       Y
75      C00060      TA02       Y
76      C00062      TA04       Y
77      C00065      TA05       Y
78      C00066      TA05       Y
79      C00067      TA03       Y
80      C00070      TA02       Y
81      C00071      TA06       Y
82      C00072      TA06       Y
83      C00073      TA01       Y
84      C00074      TA06       Y
85      C00075      TA06       Y
86      C00076      TA06       Y
87      C00077      TA03       Y
88      C00078      TA06       Y
89      C00080      TA06       Y
90      C00081      TA06       Y
91      C00082      TA06       Y
92      C00084      TA06       Y
93      C00085      TA06       Y
94      C00086      TA06       Y
95      C00087      TA06       Y
96      C00090      TA07       Y
97      C00091      TA06       Y
98      C00092      TA02       Y
99      C00093      TA03       Y
100     C00094      TA06       Y
101     C00096      TA01       Y
102     C00097      TA07       Y
103     C00098      TA07       Y
104     C00099      TA07       Y
105     C00100      TA08       Y
106     C00101      TA07       Y
107     C00103      TA07       Y
108     C00105      TA07       Y
109     C00106      TA06       Y
110     C00107      TA06       Y
111     C00109      TA09       Y
112     C00111      TA01       Y
113     C00112      TA08       Y
114     C00113      TA08       Y
115     C00114      TA08       Y
116     C00115      TA08       Y
117     C00116      TA08       Y
118     C00117      TA08       Y
119     C00118      TA08       Y
120     C00